# **Rodrigo_Mesquita_PB_TP5**
## **Projeto de Bloco: Inteligência Artificial e Machine Learning [24E1_5]**

### 1.Criação das features: Computar o Term Frequency-Inverse Document Frequency (TF-IDF) para representar a importância das palavras em um conjunto de documentos.

In [1]:
#%pip install nltk
#%pip install yellowbrick

In [2]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import nltk
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
from yellowbrick.cluster import SilhouetteVisualizer
from collections import Counter
from sklearn.metrics import silhouette_score
nltk.download("stopwords")
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/codespace/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /home/codespace/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [3]:
plt.rcParams['font.sans-serif'] = 'DejaVu Sans'

In [4]:
df = pd.read_csv('/workspaces/Faculdade/Datasets/medium.csv')
X = df['Text'].str.lower()

print(f'Quantidade de Documentos: {len(df)}')
df.head(5)

Quantidade de Documentos: 1391


Title  \
0  A Beginner’s Guide to Word Embedding with Gens...   
1  Hands-on Graph Neural Networks with PyTorch & ...   
2                       How to Use ggplot2 in Python   
3  Databricks: How to Save Data Frames as CSV Fil...   
4  A Step-by-Step Implementation of Gradient Desc...   

                                                Text  
0  1. Introduction of Word2vec\n\nWord2vec is one...  
1  In my last article, I introduced the concept o...  
2  Introduction\n\nThanks to its strict implement...  
3  Photo credit to Mika Baumeister from Unsplash\...  
4  A Step-by-Step Implementation of Gradient Desc...

In [5]:
#Aplicando Regex para manter apenas palavras com 3 ou mais caracteres, retirando pontuações e números
import re
pattern = re.compile(r"\b[a-zA-Z]{3,}\b")
X_reg = X.apply(lambda x: (' '.join(pattern.findall(str(x)))))

In [6]:
nltk.download('averaged_perceptron_tagger')


[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/codespace/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [7]:
#Leematizando o texto
data_lem = []
lemmatizer = WordNetLemmatizer()
for doc in X_reg:
  doc = doc.lower()
  doc_lem = ' '.join(lemmatizer.lemmatize(word) for word in doc.split())
  data_lem.append(doc_lem)

In [8]:
data_lem

['introduction one the most popular technique learn word embeddings using two layer neural network it input text corpus and it output set vector word embedding via can make natural language computer readable then further implementation mathematical operation word can used detect their similarity well trained set word vector will place similar word close each other that space for instance the word woman men and human might cluster one corner while yellow red and blue cluster together another there are two main training algorithm for one the continuous bag word cbow another called skip gram the major difference between these two method that cbow using context predict target word while skip gram using word predict target context generally the skip gram method can have better performance compared with cbow method for can capture two semantics for single word for instance will have two vector representation for apple one for the company and another for the fruit for more detail about the al

: 

In [9]:
#Aplicando novamente o Regex para remover palavras com menos de 3 caracteres, que surgiram após a leematização, exemplo "its" foi reduzido para "it" e está prejudicando a análise
data_lem_reg = X.apply(lambda x: (' '.join(pattern.findall(str(data_lem)))))

In [ ]:
tfidf = TfidfVectorizer(max_df=0.2, min_df=5, stop_words='english')
vect = tfidf.fit_transform(data_lem_reg)

# Convertendo a matriz TF-IDF para um DataFrame
df_tfidf = pd.DataFrame(vect.toarray(), columns= tfidf.get_feature_names_out())

# Exibindo as palavras com maior pontuação:
print(df_tfidf.loc[0].sort_values(ascending=False).head(10))

similarity    0.424331
gensim        0.328443
list          0.262889
embedding     0.204936
cosine        0.188221
sne           0.177180
item          0.173900
vehicle       0.158402
gram          0.150966
van           0.141744
Name: 0, dtype: float64


### 2.Modelagem de Tópicos com LDA: Aplicar o algoritmo LDA para identificar tópicos prevalentes nos dados. A seleção do número de tópicos será baseada em métricas de coerência para garantir a relevância e a distinção entre os tópicos identificados.

In [ ]:
#%pip install gensim
#%pip install scipy==1.12

In [ ]:
from sklearn.decomposition import LatentDirichletAllocation
from gensim.models import CoherenceModel
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from gensim import corpora, models
import pandas as pd
nltk.download('punkt')

[nltk_data] Downloading package punkt to /home/codespace/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [ ]:
# Criando o dicionário e o corpus
stop_words = stopwords.words('english')

tokens = [[word for word in doc if word not in stop_words] for doc in [word_tokenize(doc.lower()) for doc in data_lem_reg]]

dicionario = corpora.Dictionary(tokens)
dicionario.filter_extremes(no_below=5, no_above=0.3)

corpus = [dicionario.doc2bow(doc) for doc in tokens]

# Treinando o modelo LDA
modelo_lda = models.LdaModel(corpus, num_topics=6, id2word=dicionario, passes=10)

# Exibindo os tópicos
for idx, topic in modelo_lda.print_topics():
    print(f"Tópico {idx}: {topic}")

# Calcular métricas de coerência 
from gensim.models import CoherenceModel
coherence_model_lda = CoherenceModel(model=modelo_lda, texts=tokens, dictionary=dicionario, coherence="u_mass")
coherence_lda = coherence_model_lda.get_coherence()
print(f"Coerência do modelo LDA: {coherence_lda:.4f}")

Tópico 0: 0.025*"model" + 0.011*"data" + 0.007*"time" + 0.007*"learning" + 0.006*"value" + 0.005*"using" + 0.005*"one" + 0.004*"feature" + 0.004*"machine" + 0.004*"use"
Tópico 1: 0.009*"data" + 0.009*"file" + 0.009*"model" + 0.008*"code" + 0.008*"function" + 0.007*"use" + 0.007*"image" + 0.007*"python" + 0.006*"using" + 0.005*"need"
Tópico 2: 0.021*"data" + 0.016*"model" + 0.010*"value" + 0.008*"feature" + 0.006*"one" + 0.006*"learning" + 0.006*"set" + 0.005*"algorithm" + 0.005*"use" + 0.005*"number"
Tópico 3: 0.027*"data" + 0.006*"science" + 0.006*"wa" + 0.005*"one" + 0.005*"time" + 0.005*"learning" + 0.005*"ha" + 0.004*"people" + 0.004*"like" + 0.004*"machine"
Tópico 4: 0.011*"model" + 0.009*"data" + 0.008*"learning" + 0.005*"image" + 0.005*"machine" + 0.005*"human" + 0.005*"wa" + 0.004*"ha" + 0.004*"one" + 0.004*"algorithm"
Tópico 5: 0.009*"image" + 0.008*"function" + 0.008*"word" + 0.008*"data" + 0.007*"model" + 0.006*"using" + 0.006*"layer" + 0.006*"network" + 0.005*"value" + 0.00

### 3.Classificação de Textos: Desenvolver modelos de classificação para categorizar os textos com base nos tópicos identificados. Você pode escolher qualquer modelo aprendido ao longo do curso e deve escolher o melhor modelo usando as técnicas aprendidas, como busca de hiperparâmetros e validação cruzada

### 4.Avaliação de Desempenho: O desempenho dos modelos de classificação será avaliado utilizando métricas como precisão, recall, F1-score e AUC-ROC.

### 5.Visualização com t-SNE: Aplicar a técnica de t-SNE nos dados textuais vetorizados para reduzir a dimensionalidade e visualizar os agrupamentos de documentos de maneira intuitiva, facilitando a identificação de padrões e outliers.

### 6.Interpretação de Modelos com LIME, SHAP e Force-Plot: Utilizar SHAP para explicar as previsões individuais, identificando a contribuição de cada feature para a decisão do modelo. O force-plot será usado para visualizar essas contribuições de maneira agregada, oferecendo insights sobre a lógica de decisão do modelo.

### 7.Análise dos resultados: Enumere as conclusões que podem ser tomadas a partir dos resultados obtidos.

### 8.Ambiente Recomendado: A solução pode ser desenvolvida em qualquer ambiente de sua escolha, embora seja recomendado o uso do Google Colab Notebook. Lembre-se de comentar seu código para facilitar a compreensão da análise e do procedimento adotado.